In [ ]:
pip install osmnx

In [1]:
import pandas as pd
import requests
import geopandas as gpd
import csv
import plotly.express as px
import folium
import pandas as pd
from folium.plugins import MarkerCluster
import json
from shapely.geometry import shape, Point
import matplotlib . pyplot as plt
from sqlalchemy import create_engine
from sqlalchemy . sql import text
import osmnx

abfrage aller Sense-Boxen in einem bestimmten Gebiet

In [28]:
url = "https://api.opensensemap.org/boxes?near=10.323007,51.16501&maxDistance=450000&exposure=outdoor&title=PM10,PM2.5&format=geojson"
data = requests.get(url).json()
df = pd.DataFrame(data)
data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'_id': '5cfe574ba1ba9f001a129dd1',
    'createdAt': '2022-03-30T11:25:43.734Z',
    'updatedAt': '2022-08-20T14:16:27.405Z',
    'name': 'CarportSensor1',
    'exposure': 'outdoor',
    'sensors': [{'title': 'PM10',
      'unit': 'µg/m³',
      'sensorType': 'SDS 011',
      'icon': 'osem-cloud',
      '_id': '5cfe574ba1ba9f001a129dd5',
      'lastMeasurement': '6300ecb93e63e3001b7de561'},
     {'title': 'PM2.5',
      'unit': 'µg/m³',
      'sensorType': 'SDS 011',
      'icon': 'osem-cloud',
      '_id': '5cfe574ba1ba9f001a129dd4',
      'lastMeasurement': '6300ecb93e63e3001b7de562'},
     {'_id': '5cfe574ba1ba9f001a129dd3',
      'title': 'Temperatur',
      'unit': '°C',
      'sensorType': 'DS18B20',
      'icon': 'osem-thermometer',
      'lastMeasurement': '6300ecb93e63e3001b7de563'},
     {'_id': '5cfe574ba1ba9f001a129dd2',
      'title': 'Luftdruck',
      'unit': 'Pa',
      'sensorType': 'BMP28

Erstellung eines GeoDataFrames anhand der zuvor erfolgten Abfrage

In [31]:
extracted_data = []

#dataframe
coordinates = {"id": [],
                  "latitude": [],
                  "longitude": []
                }
df_coordinates = pd.DataFrame(coordinates)
    
# Iteriere durch alle Features in den Daten
for idx in range(len(data["features"])):
    feature = data["features"][idx]
    sensors = feature["properties"]["sensors"]
    
    # Suche den PM10-Sensor in der Liste der Sensoren
    pm10_sensor = next((sensor for sensor in sensors if sensor["title"] == "PM10"), None)
    # Suche den PM10-Sensor in der Liste der Sensoren
    pm2_5_sensor = next((sensor for sensor in sensors if sensor["title"] == "PM2.5"), None)
    
    # Wenn der PM10-Sensor gefunden wurde, extrahiere die benötigten Informationen
    if pm10_sensor and pm2_5_sensor:
        df2 = {
            "id": feature["properties"]["_id"],
            "latitude": feature["geometry"]["coordinates"][1],
            "longitude": feature["geometry"]["coordinates"][0],
            "id_PM10_Messung": pm10_sensor["_id"],
            "id_PM2_5_Messung" : pm2_5_sensor["_id"],  
            "created_at": feature["properties"]["createdAt"],
            "updated_at": feature["properties"]["updatedAt"]
        }
        extracted_data.append(df2)
    df_coordinates = df_coordinates._append(df2, ignore_index = True)


gdf = gpd.GeoDataFrame(
    df_coordinates, geometry=gpd.points_from_xy(df_coordinates.longitude, df_coordinates.latitude), crs="EPSG:4326")

gdf['updated_at'] = pd.to_datetime(gdf['updated_at'])

# Konvertiere die datetime-Objekte in das gewünschte Format
gdf['updated_at'] = gdf['updated_at'].dt.strftime('%Y-%m-%dT')

gdf = gdf.drop_duplicates(subset=['id'])

sorted_gdf = gdf.sort_values(by=['updated_at', 'created_at'], ascending=[False, True])
sorted_gdf

id   latitude  longitude  \
1706  58b9b3fb380530000f42d745  51.436012   7.292953   
3668  598b2f86e3b1fa0010f0f8d4  49.154591   8.252921   
3635  5ac158fb850005001bae6beb  53.560386  10.061604   
4713  5df532463a2923001fde4f64  53.011743  13.994345   
4481  5e1f8e25b459b2001e04b723  48.392838   9.960061   
...                        ...        ...        ...   
1679  5fd7acb70cc45d001bb9abf7  49.500233  11.753378   
1657  5b366bc01fef04001b0e8e06  51.440464   7.331547   
3452  5fc5034ac949b9001b18c241  52.635658  13.327675   
2023  5fcb762afab469001c180325  51.666041   7.154988   
4415  5f9314e2321dc8001bf79e86  49.608753   6.771670   

               id_PM10_Messung          id_PM2_5_Messung  \
1706  58d8036ab69fac001120052c  58d8036ab69fac001120052d   
3668  598b2f86e3b1fa0010f0f8d8  598b2f86e3b1fa0010f0f8d7   
3635  5ac158fb850005001bae6bef  5ac158fb850005001bae6bee   
4713  5df532463a2923001fde4f66  5df532463a2923001fde4f65   
4481  5e20a910877b31001a3aed41  5e20a910877b31001a3aed42   
...                        ...                       ...   
1679  5fd7acb70cc45d001bb9abfc  5fd7acb70cc45d001bb9abfb   
1657  5b366bc01fef04001b0e8e08  5b366bc01fef04001b0e8e07   
3452  5fc5034ac949b9001b18c247  5fc5034ac949b9001b18c246   
2023  5fcb762afab469001c180329  5fcb762afab469001c18032a   
4415  5f9314e2321dc8001bf79e8a  5f9314e2321dc8001bf79e8b   

                    created_at   updated_at                   geometry  
1706  2017-03-03T18:20:43.179Z  2024-05-31T   POINT (7.29295 51.43601)  
3668  2017-08-09T15:51:34.754Z  2024-05-31T   POINT (8.25292 49.15459)  
3635  2018-04-01T22:11:07.375Z  2024-05-31T  POINT (10.06160 53.56039)  
4713  2019-12-14T19:04:38.594Z  2024-05-31T  POINT (13.99434 53.01174)  
4481  2020-01-15T22:11:49.310Z  2024-05-31T   POINT (9.96006 48.39284)  
...                        ...          ...                        ...  
1679  2020-12-14T18:19:35.828Z  2020-12-14T  POINT (11.75338 49.50023)  
1657  2018-06-29T17:26:24.294Z  2020-12-09T   POINT (7.33155 51.44046)  
3452  2020-11-30T14:35:54.220Z  2020-12-06T  POINT (13.32767 52.63566)  
2023  2020-12-05T11:59:38.994Z  2020-12-05T   POINT (7.15499 51.66604)  
4415  2020-10-23T17:37:38.026Z  2020-10-23T   POINT (6.77167 49.60875)  

[4400 rows x 8 columns]

Es werden nur die Werte herausgesucht, die auch innerhalb Deutschlands liegen

In [ ]:
# Lade die Grenzen von Deutschland von OpenStreetMap
landesgrenzen = ox.geocode_to_gdf("Germany")

for index, row in gdf.iterrows():
    coordinates = row['geometry']
    id_value = row['id']

    # Überprüfen, ob der Punkt innerhalb der Landgrenzen von Deutschland liegt
    if not landesgrenzen.geometry.contains(coordinates).any():
        # Lösche die Zeile basierend auf dem Index
        gdf.drop(index, inplace=True)

nun werden die Sense-Boxen betrachtet, die noch aktuell und am Ältesten sind und händisch untersucht, um 10 geeignete zu finden, die untersucht werden

In [34]:
gdf['updated_at'] = pd.to_datetime(gdf['updated_at'])

# Konvertiere die datetime-Objekte in das gewünschte Format
gdf['updated_at'] = gdf['updated_at'].dt.strftime('%Y-%m-%dT')


sorted_gdf = gdf.sort_values(by=['updated_at', 'created_at'], ascending=[False, True])
sorted_gdf.head(30)

id   latitude  longitude  \
1706  58b9b3fb380530000f42d745  51.436012   7.292953   
3668  598b2f86e3b1fa0010f0f8d4  49.154591   8.252921   
3635  5ac158fb850005001bae6beb  53.560386  10.061604   
4713  5df532463a2923001fde4f64  53.011743  13.994345   
4481  5e1f8e25b459b2001e04b723  48.392838   9.960061   
2448  5e5aed0fe8fdda001b1528e5  49.202318   8.984893   
1278  5f4542b8badf01001bd5cf24  51.910651   7.723412   
5445  5f91ec3683f564001b37ec11  51.320843   4.952198   
5415  5f9d265b46592b001bec475c  52.382577   5.270664   
3748  5f9f0e5b53295c001baf67dd  53.590727  10.053233   
2160  5fa29e9067d8a1001bd07a2c  50.987335   7.037762   
5572  5fa3fc2867d8a1001b5f9d6d  52.340481   4.961538   
3227  5fa5cae667d8a1001b1e3fe6  52.500826  13.431521   
4973  5fa6e60b67d8a1001b969275  54.091347  12.123221   
4971  5fa7e9b667d8a1001b056958  54.093341  12.111397   
5819  5fa916fd67d8a1001b851de6  52.737995   4.751748   
5420  5fa96a8567d8a1001ba916c7  53.223937   5.999606   
3488  5fad60d49b2df8001b04ec23  52.587957  13.394083   
5367  5fb143a69b2df8001bb4a8e8  48.023826   8.773506   
4261  5fb65cc67a70a5001cc16162  51.097730  14.506950   
4863  5fb6d6e87a70a5001cf716e8  51.485537   5.435778   
2278  5fb7de317a70a5001c6af2da  52.379537  13.092337   
2622  5fba6fe67a70a5001c8c169c  50.937000   6.853000   
3940  5fbce7527a70a5001ca6cfe4  49.397593   7.613157   
2679  5fbea3b87a70a5001c6c170c  51.003806   6.812192   
5351  5fbed0927a70a5001c80494f  48.131007   8.377310   
4816  5fbfe4b0eb7b78001c1059f7  49.586737   6.260517   
5002  5fc261f13a7437001bda419a  48.119613  11.482455   
1312  5fc4d0a4c949b9001b01b72d  51.462076   7.479813   
4683  5fc50143c949b9001b17db7b  51.980567   5.850325   

               id_PM10_Messung          id_PM2_5_Messung  \
1706  58d8036ab69fac001120052c  58d8036ab69fac001120052d   
3668  598b2f86e3b1fa0010f0f8d8  598b2f86e3b1fa0010f0f8d7   
3635  5ac158fb850005001bae6bef  5ac158fb850005001bae6bee   
4713  5df532463a2923001fde4f66  5df532463a2923001fde4f65   
4481  5e20a910877b31001a3aed41  5e20a910877b31001a3aed42   
2448  5e5aed0fe8fdda001b1528e7  5e5aed0fe8fdda001b1528e6   
1278  5f4542b8badf01001bd5cf29  5f4542b8badf01001bd5cf28   
5445  5f91ec3683f564001b37ec15  5f91ec3683f564001b37ec14   
5415  5f9d265b46592b001bec4761  5f9d265b46592b001bec4760   
3748  5f9f0e5b53295c001baf67e2  5f9f0e5b53295c001baf67e1   
2160  5fa2a41e67d8a1001bd2db0d  5fa2a41e67d8a1001bd2db0e   
5572  5fa3fc2867d8a1001b5f9d72  5fa3fc2867d8a1001b5f9d71   
3227  5fa5cae667d8a1001b1e3feb  5fa5cae667d8a1001b1e3fea   
4973  5fa6e60b67d8a1001b96927a  5fa6e60b67d8a1001b969279   
4971  5fa7e9b667d8a1001b05695d  5fa7e9b667d8a1001b05695c   
5819  5fa916fd67d8a1001b851deb  5fa916fd67d8a1001b851dea   
5420  5fa96a8567d8a1001ba916cc  5fa96a8567d8a1001ba916cb   
3488  5fad60d49b2df8001b04ec28  5fad60d49b2df8001b04ec27   
5367  5fb143a69b2df8001bb4a8ed  5fb143a69b2df8001bb4a8ec   
4261  5fb65cc67a70a5001cc16166  5fb65cc67a70a5001cc16165   
4863  5fb6d6e87a70a5001cf716ed  5fb6d6e87a70a5001cf716ec   
2278  5fb7de317a70a5001c6af2dc  5fb7de317a70a5001c6af2db   
2622  5fba6fe67a70a5001c8c16a0  5fba6fe67a70a5001c8c169f   
3940  5fbce7527a70a5001ca6cfe8  5fbce7527a70a5001ca6cfe7   
2679  5fbea3b87a70a5001c6c1710  5fbea3b87a70a5001c6c170f   
5351  5fbed0927a70a5001c804954  5fbed0927a70a5001c804953   
4816  5fbfe4b0eb7b78001c1059fb  5fbfe4b0eb7b78001c1059fa   
5002  5fc261f13a7437001bda419e  5fc261f13a7437001bda419d   
1312  5fc4d0a4c949b9001b01b731  5fc4d0a4c949b9001b01b730   
4683  5fc50143c949b9001b17db80  5fc50143c949b9001b17db7f   

                    created_at   updated_at                   geometry  
1706  2017-03-03T18:20:43.179Z  2024-05-31T   POINT (7.29295 51.43601)  
3668  2017-08-09T15:51:34.754Z  2024-05-31T   POINT (8.25292 49.15459)  
3635  2018-04-01T22:11:07.375Z  2024-05-31T  POINT (10.06160 53.56039)  
4713  2019-12-14T19:04:38.594Z  2024-05-31T  POINT (13.99434 53.01174)  
4481  2020-01-15T22:11:49.310Z  2024-05-31T   POINT (9.96006 48.3

das sind die gefundenen Sense-Boxen

In [35]:
open_sense_box_land = ['598b2f86e3b1fa0010f0f8d4', '5fb143a69b2df8001bb4a8e8', '5fb65cc67a70a5001cc16162', '5df532463a2923001fde4f64', '5fbed0927a70a5001c80494f']
open_sense_box_land_sensor_PM10 = ['598b2f86e3b1fa0010f0f8d8', '5fb143a69b2df8001bb4a8ed', '5fb65cc67a70a5001cc16166', '5df532463a2923001fde4f66', '5fbed0927a70a5001c804954']
open_sense_box_land_sensor_PM2_5 = ['598b2f86e3b1fa0010f0f8d7', '5fb143a69b2df8001bb4a8ec', '5fb65cc67a70a5001cc16165', '5df532463a2923001fde4f65', '5fbed0927a70a5001c804953']
open_sense_box_stadt = ['5ac158fb850005001bae6beb', '5fc261f13a7437001bda419a', '5fa5cae667d8a1001b1e3fe6', '5fa6e60b67d8a1001b969275', '5fba6fe67a70a5001c8c169c']
open_sense_box_stadt_sensor_PM10 = ['5ac158fb850005001bae6bef', '5fc261f13a7437001bda419e', '5fa5cae667d8a1001b1e3feb', '5fa6e60b67d8a1001b96927a', '5fba6fe67a70a5001c8c16a0']
open_sense_box_stadt_sensor_PM2_5 = ['5ac158fb850005001bae6bee', '5fc261f13a7437001bda419d', '5fa5cae667d8a1001b1e3fea', '5fa6e60b67d8a1001b969279', '5fba6fe67a70a5001c8c169f']

Nun wird die API-Abfrage durchgeführt. Hierfür wird über alle Jahre, alle Monate und eine bestimmte Anzahl an Tagen iteriert und die Werte extrahiert. Das alles passiert zur gleichen Uhrzeit an den Tagen. Um 12 Uhr mittags.

Achtung nach einiger Zeit kommt ein TimeoutFehler, daher wurde es im Codeblock unterhalb ohne die äußerste for-Schleife durchgeführt.

In [ ]:
# Initialisiere ein leeres DataFrame, um die Daten aller Anfragen zu speichern
big_df = pd.DataFrame()

jahre = ["2020", "2021", "2022", "2023", "2024"]
monate = ["01", "02", "03", "04", "05", "06", "07", "08", "09", "10", "11", "12"]
tage = ["01", "03", "05", "07", "09", "11", "13", "15", "17", "19", "21", "23", "25", "27", "29"]

x = 0

# Iteriere über jede Zeile im GeoDataFrame
for box_id, sensor_id in zip(open_sense_box_land, open_sense_box_land_sensor):

    x += 1

    exec(f"df_box_{x} = pd.DataFrame()")
    
    for jahr in jahre:
        for monat in monate:
            for tag in tage:
                url = f"https://api.opensensemap.org/boxes/{box_id}/data/{sensor_id}?from-date={jahr}-{monat}-{tag}T12:00:00.000Z&to-date={jahr}-{monat}-{tag}T12:02:00.000Z&download=true&format=json"
    
                response = requests.get(url)
    
                if response.status_code == 200:
                    # Erfolgreiche Anfrage
                    data = response.json()

                    if data == []:
                        continue

                    else:
                        df = pd.DataFrame(data)
                        df['createdAt'] = pd.to_datetime(df['createdAt'])

                        # Konvertiere die datetime-Objekte in das gewünschte Format
                        df['createdAt'] = df['createdAt'].dt.strftime('%Y-%m-%dT')
                        df["value"] = pd.to_numeric(df['value'])
                        df["id"] = box_id
                        df.drop(columns=["location"], inplace=True)
        
                        # Daten zum großen DataFrame hinzufügen
                        exec("df_box_{x} = pd.concat([df_box_{x}, df], ignore_index=True)")
        
        print(f"jahr {jahr} done")
    
    print(f"box {box_id} done")

    exec(f"df_box_{x}.set_index('createdAt', inplace=True)")

# Merge die DataFrames basierend auf dem Index (createdAt)
merged_df = df_box_1.merge(df_box_2, on='createdAt', how='outer')
merged_df = merged_df.merge(df_box_3, on='createdAt', how='outer')
merged_df = merged_df.merge(df_box_4, on='createdAt', how='outer')
merged_df = merged_df.merge(df_box_5, on='createdAt', how='outer')

In [49]:
box_id = '5fba6fe67a70a5001c8c169c'
sensor_id = '5fba6fe67a70a5001c8c169f'

jahre = ["2020", "2021", "2022", "2023", "2024"]
monate = ["01", "02", "03", "04", "05", "06", "07", "08", "09", "10", "11", "12"]
tage = ["01", "03", "05", "07", "09", "11", "13", "15", "17", "19", "21", "23", "25", "27", "29"]

x = 5
exec(f"df_box_{x} = pd.DataFrame()")

for jahr in jahre:
    for monat in monate:
        for tag in tage:
            url = f"https://api.opensensemap.org/boxes/{box_id}/data/{sensor_id}?from-date={jahr}-{monat}-{tag}T12:00:00.000Z&to-date={jahr}-{monat}-{tag}T12:02:00.000Z&download=true&format=json"
 
            response = requests.get(url)
   
            if response.status_code == 200:
                # Erfolgreiche Anfrage
                data = response.json()

                if data == []:
                    continue

                else:
                    df = pd.DataFrame(data)
                    df['createdAt'] = pd.to_datetime(df['createdAt'])

                    # Konvertiere die datetime-Objekte in das gewünschte Format
                    df['createdAt'] = df['createdAt'].dt.strftime('%Y-%m-%dT')
                    df["value"] = pd.to_numeric(df['value'])
                    df["id"] = box_id
                    df.drop(columns=["location"], inplace=True)
     
                    # Daten zum großen DataFrame hinzufügen
                    exec(f"df_box_{x} = pd.concat([df_box_{x}, df], ignore_index=True)")
        
    print(f"jahr {jahr} done")
    
print(f"box {box_id} done")

exec(f"df_box_{x}.set_index('createdAt', inplace=True)")

jahr 2020 done
jahr 2021 done
jahr 2022 done
jahr 2023 done
jahr 2024 done
box 5fba6fe67a70a5001c8c169c done


nun werden die Spalten der einzelnen erstellten DataFrames umbenannt, um das zusammenführen zu vereinfachen

In [50]:
# Spalte umbenennen
df_box_1.rename(columns={"value": "value_1"}, inplace=True)
df_box_1.rename(columns={"id": "id_1"}, inplace=True)
df_box_2.rename(columns={"value": "value_2"}, inplace=True)
df_box_2.rename(columns={"id": "id_2"}, inplace=True)
df_box_3.rename(columns={"value": "value_3"}, inplace=True)
df_box_3.rename(columns={"id": "id_3"}, inplace=True)
df_box_4.rename(columns={"value": "value_4"}, inplace=True)
df_box_4.rename(columns={"id": "id_4"}, inplace=True)
df_box_5.rename(columns={"value": "value_5"}, inplace=True)
df_box_5.rename(columns={"id": "id_5"}, inplace=True)

die DataFrames werden zu einem zusammengeführt

In [51]:
# Merge die DataFrames basierend auf dem Index (createdAt)
merged_df = df_box_1.merge(df_box_2, on='createdAt', how='outer')
merged_df = merged_df.merge(df_box_3, on='createdAt', how='outer')
merged_df = merged_df.merge(df_box_4, on='createdAt', how='outer')
merged_df = merged_df.merge(df_box_5, on='createdAt', how='outer')
# Index zurücksetzen und Datum in eine Spalte verschieben
merged_df.reset_index(inplace=True)
merged_df.rename(columns={'index': 'created_at'}, inplace=True)
merged_df

createdAt  value_1                      id_1  value_2  \
0    2022-04-07T     1.40  5ac158fb850005001bae6beb      NaN   
1    2022-04-07T     1.40  5ac158fb850005001bae6beb      NaN   
2    2022-04-07T     1.40  5ac158fb850005001bae6beb      NaN   
3    2022-04-09T     1.67  5ac158fb850005001bae6beb     1.60   
4    2022-04-09T     1.67  5ac158fb850005001bae6beb     1.60   
..           ...      ...                       ...      ...   
870  2024-05-21T      NaN                       NaN     0.80   
871  2024-05-23T      NaN                       NaN     1.80   
872  2024-05-25T     6.50  5ac158fb850005001bae6beb     0.98   
873  2024-05-27T     3.20  5ac158fb850005001bae6beb     2.47   
874  2024-05-29T     2.47  5ac158fb850005001bae6beb      NaN   

                         id_2  value_3                      id_3  value_4  \
0                         NaN     1.90  5fa5cae667d8a1001b1e3fe6     1.33   
1                         NaN     1.90  5fa5cae667d8a1001b1e3fe6     1.33   
2                         NaN     1.90  5fa5cae667d8a1001b1e3fe6     1.33   
3    5fc261f13a7437001bda419a     1.80  5fa5cae667d8a1001b1e3fe6     0.90   
4    5fc261f13a7437001bda419a     1.80  5fa5cae667d8a1001b1e3fe6     0.90   
..                        ...      ...                       ...      ...   
870  5fc261f13a7437001bda419a     5.40  5fa5cae667d8a1001b1e3fe6      NaN   
871  5fc261f13a7437001bda419a     3.80  5fa5cae667d8a1001b1e3fe6      NaN   
872  5fc261f13a7437001bda419a      NaN                       NaN    24.03   
873  5fc261f13a7437001bda419a     2.80  5fa5cae667d8a1001b1e3fe6     5.70   
874                       NaN     2.03  5fa5cae667d8a1001b1e3fe6     1.77   

                         id_4  value_5                      id_5  
0    5fa6e60b67d8a1001b969275     1.20  5fba6fe67a70a5001c8c169c  
1    5fa6e60b67d8a1001b969275     1.13  5fba6fe67a70a5001c8c169c  
2    5fa6e60b67d8a1001b969275     1.00  5fba6fe67a70a5001c8c169c  
3    5fa6e60b67d8a1001b969275     2.33  5fba6fe67a70a5001c8c169c  
4    5fa6e60b67d8a1001b969275     3.30  5fba6fe67a70a5001c8c169c  
..                        ...      ...                       ...  
870                       NaN      NaN                       NaN  
871                       NaN      NaN                       NaN  
872  5fa6e60b67d8a1001b969275     2.00  5fba6fe67a70a5001c8c169c  
873  5fa6e60b67d8a1001b969275     2.10  5fba6fe67a70a5001c8c169c  
874  5fa6e60b67d8a1001b969275      NaN                       NaN  

[875 rows x 11 columns]

nun wird eine Verbindung zur Datenbank hergestellt und sowohl die Tabelle mit den einzelnen Senseboxen, als auch die Tabellen mit den Werten werden abgespeichert.

In [52]:
user = "postgres"
password = "PhysikImAdvent20"
host = "localhost"
port = 5432
database = "projekt"

connection = f"postgresql://{user}:{password}@{host}:{port}/{database}"
engine = create_engine(connection)

# Schreibe das DataFrame in die PostGIS-Datenbank
merged_df.to_sql(name="werte_stadt_PM2_5", con=engine, schema="public", if_exists="replace", index=False)

# gdf.to_postgis(name = "sense_boxen", con=engine , schema ="public")

875

Dies könnte benutzt werden, um zu überprüfen, ob eine SenseBox auf dem Land oder in einer Stadt steht, aber der Code benötigt schon für diesen einzelnen Punkt über 10 Minuten. Bei 3000 Punkten, wäre es mit unseren begrenzten Mitteln nicht machbar.

In [ ]:
# Laden Sie das Straßennetzwerk für Deutschland herunter
graph = ox.graph_from_place("Germany", network_type='all')

# Definieren Sie den Punkt
punkt = Point(13.4050, 52.5200)  # Beispielkoordinaten für Berlin

# Laden Sie die Stadtgrenzen für Deutschland herunter
stadtgrenzen = osmnx.geocode_to_gdf("Germany")

# Überprüfen Sie, ob der Punkt in einer Stadt liegt
for index, row in stadtgrenzen.iterrows():
    if row['geometry'].contains(punkt):
        print("Der Punkt liegt in der Stadt:", row['name'])
        break
else:
    print("Der Punkt liegt nicht in einer Stadt in Deutschland.")

eine Karte von Deutschland, auf der alle eingetragenen SenseBoxen zu sehen ist.

In [9]:
map_deutschland = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

# Marker Cluster erstellen
marker_cluster = MarkerCluster().add_to(map_deutschland)

for index, row in gdf.iterrows():
    point = row.geometry  # Annahme: Die geometrische Spalte heißt 'geometry'
    latitude = point.y
    longitude = point.x
    folium.Marker(location=[latitude, longitude], popup=row['id']).add_to(marker_cluster)

    
map_deutschland